# Exercise 5: Image classification - Part 2

## 1. Install dependencies, if needed

Run the commands below to install the dependencies

In [ ]:
!pip install -q pillow matplotlib scikit-image scikit-learn gdown

## 2. Extract regions and features

- Download the images by running the next cell

In [ ]:
import zipfile
import gdown
import os

if not os.path.exists("images_week5"):
    id = "1_ZeK5eEZQqenYK-mIdIAcLS66mwfKGBg"
    gdown.download(id=id, output="images_week5.zip", quiet=True)
    with zipfile.ZipFile("images_week5.zip", 'r') as zip_ref:
        zip_ref.extractall()
    
print(os.listdir("images_week5"))

- Alternatively, download the images from [here](https://drive.google.com/file/d/1_ZeK5eEZQqenYK-mIdIAcLS66mwfKGBg/view?usp=sharing). 

- The zip file contains the following subfolders:
    - images
    - gt: Ground truth (GT) labels for each pixel of the image, labeled with the following classes
        - 0. Impervious
        - 1. Building
        - 2. Low vegetation
        - 3. Tree
- Extract features (average, standard deviation and histogram of each band)
- Extract and save regions for each image using SLIC (use the parameter n_segments=1000)
- Extract and save features for the regions of each image

In [ ]:
# The following functions are the same you implemented the past week
# You do not need to edit the functions of this code block (just run it)
def convert_to_shape_pixels_by_bands(data):
    num_dimensions = len(data.shape)
    assert(num_dimensions == 2 or num_dimensions == 3)
    if num_dimensions == 3:
        num_bands = data.shape[2]
        return data.reshape((-1, num_bands))
    else:
        return data

def compute_average_feature(data):
    # If needed convert data to the shape (num_pixels x num_bands)
    data_2d = convert_to_shape_pixels_by_bands(data)
    num_bands = data_2d.shape[1]
    avg_features = np.mean(data_2d, axis=0)
    return avg_features

def compute_standard_deviation_feature(data):
    # If needed convert data to the shape (num_pixels x num_bands)
    data_2d = convert_to_shape_pixels_by_bands(data)
    avg_features = np.std(data_2d, axis=0)
    return avg_features

def compute_histogram_feature(data, num_bins=10):
    # If needed convert data to the shape (num_pixels x num_bands)
    data_2d = convert_to_shape_pixels_by_bands(data)
    num_bands = data_2d.shape[1]
    hist_features = np.zeros((num_bands, num_bins)).astype(np.float32)
    for b in range(num_bands):
        # Compute the histogram for each band 
        #       use the function np.histogram(array, bins=num_bins)
        hist, boundaries = np.histogram(data_2d[:, b], bins=num_bins)
        hist_features[b, :] = hist
    # Return a 1D array containing all the values
    return hist_features.flatten()

def compute_image_features_from_regions(image, segmentation_map):
    num_regions = len(np.unique(segmentation_map))
    all_features = []
    for id_region in range(num_regions):
        # Obtain pixel values of each regions, with shape (num_pixels x num_bands)
        pixel_values = image[segmentation_map==id_region]
        # Compute the average, standard deviation and histogram features
        #       and concatenated them unsing the function (np.concatenate)
        avg = compute_average_feature(pixel_values)
        features = compute_standard_deviation_feature(pixel_values)
        hist_features = compute_histogram_feature(pixel_values)
        features = np.concatenate([avg, features, hist_features])
        # Add concatenated features to the variable all_features
        all_features.append(features)
    # convert list to numpy array of shape: (num_regions x num_bands)
    return np.array(all_features).astype(np.float32)

In [ ]:
import numpy as np
from skimage.io import imsave, imread
from skimage.segmentation import slic

# TODO: Fill the path of the dataset (e.g., "images_week5/")
input_dir = 

total_num_images = 9
for image_number in range(1, total_num_images + 1):
    # TODO: Read image
    image_path = 
    image = imread(image_path)
    # TODO: Segment image using SLIC (use the parameter n_segments=1000, and start_label=0)
    segmented_image = 
    # Save SLIC regions
    regions_path = input_dir + "regions/regions_" + str(image_number) + ".tif"
    imsave(regions_path, segmented_image.astype(np.uint32))
    print("Regions saved in " + regions_path)
    # TODO: Compute features with the function compute_image_features_from_regions
    region_features = 
    # Save features
    region_features_path = input_dir + "features/features_" + str(image_number) + ".npy"
    np.save(region_features_path, region_features)
    print("Features saved in " + region_features_path)

## 3. Create training dataset
- Define which images will be in the training, test, and validation set
- Read the images from the training set and compute the ideal label for each region (the label that has the largest intersection with each region)
- Create an array of targets (groud truth), per region, that joins the targets of all the training images
- Create an array of features that joins the features of all the training images

In [2]:
# Defining which images will belong to the train, test, and validation sets
train_image_numbers = [1 ,2, 3] 
test_image_numbers = [4, 5, 6]
validation_image_numbers = [7, 8, 9]

In [ ]:
def get_label_per_region(segmented_image, label_map):
    """
    Returns a 1D numpy array that contains the label for each region, shape: (num_regions)
            For each region, we obtain the label that has the largest intersection with it
    """
    num_regions = len(np.unique(segmented_image))
    num_labels = len(np.unique(label_map))
    region_labels = []
    for region_id in range(num_regions):
        mask_region = segmented_image == region_id
        
        intersection_per_label = []
        for label_id in range(num_labels):
            mask_label = label_map == label_id
            # Compute intersection of each region with each label
            intersection = np.sum(mask_region * mask_label)
            intersection_per_label.append(intersection)
        
        intersection_per_label = np.array(intersection_per_label)
        # Obtain the index of the label with largest intersection
        selected_label = np.argmax(intersection_per_label)
        region_labels.append(selected_label)
    
    return np.array(region_labels).astype(np.uint32)

In [ ]:
import numpy as np
from skimage.io import imsave, imread

# Create arrays of training targets and features 
all_train_region_features = []
all_train_region_labels = []

for image_number in train_image_numbers:
    # TODO: read segmented image
    segmented_image_path = 
    segmented_image = 
    # TODO: read ground truth image
    gt_path = 
    gt_image = 
    # TODO: Get labels per region using the function "get_label_per_region" defined above
    region_labels = 
    # Add current region labels to the variable all_train_region_labels
    all_train_region_labels.append(region_labels)
    # TODO: read features using the function: np.load(file_path.npy)
    region_features_path = 
    region_features = 
    # Add current region features to the variable all_train_region_features
    all_train_region_features.append(region_features)

# Tranforming the list all_train_region_labels in an array of shape: (num_all_regions)
train_labels = np.concatenate(all_train_region_labels)
print("train_labels shape " + str(train_labels.shape))
# Tranforming the list all_train_region_features in an array of shape: (num_all_regions, num_features)
train_features = np.concatenate(all_train_region_features)
print("train_features shape " + str(train_features.shape))

## 4. Normalize features of the training set

Normalize features by substracting the mean and dividing by the standard deviation

In [ ]:
mean_per_feature = np.mean(train_features, axis=0)
std_per_feature = np.std(train_features, axis=0)
# TODO: normalize features by substracting the mean and dividing by the standard deviation
norm_train_features = 

## 5. Train Random Forest classifier with default parameters

Train Random Forest model using the ***sklearn*** library (use the parameter random_state=10)

In [ ]:
from sklearn.ensemble import RandomForestClassifier

# TODO: create random forest classifier with the parameter random_state=10
classifier = 
# TODO: fit the model with the normalized features (use the function fit() )


## 6. Implement a function to predict the classification maps of a set of images

Implement a function ***predict_classification_maps_and_get_accuracy*** that takes as input
- a trained classifier
- a list of image numbers
- the input directory, 
- mean value per feature (used for feature normalization),
- standard deviation value per feature (used for feature normalization),
- a boolean paramater save_predictions that determines if prediction needs to be saved

and returns the accuracy and confusion matrix

Read the documentation of ***sklearn*** to use functions that compute the accuracy and confusion matrix


In [ ]:
import matplotlib.pyplot as plt

def predict_classification_maps_and_get_accuracy(classifier, image_numbers, input_dir, 
                                                 mean_per_feature, std_per_feature, save_predictions=False):
    list_predictions = []
    list_gt_labels = []
    for image_number in image_numbers:
        # Compute predicted classification map "predicion_map" using the trained classifier
        # TODO: Read segmented image
        segmented_image_path = 
        segmented_image = 
        # TODO: Read features using the function: np.load(file_path.npy)
        region_features_path = 
        region_features = 
        # TODO: Normalize features by substracting the mean and dividing by the standard deviation (of the train set) 
        norm_region_features = 
        # TODO: Predict label of regions (use the function "predict")
        label_predictions = 
        # TODO: Compute label predictions per pixel
        predicion_map = np.zeros(segmented_image.shape).astype(np.uint8)
        num_regions = len(np.unique(segmented_image))
        for region_id in range(num_regions):
            # Set the label predicted for a region to all the pixels of that region
            
        
        
        # TODO: Append predictions "prediction_map" to "list_predictions" (flatten the array before appending)
        
        
        if save_predictions:
            # TODO: Save prediction map image "predicion_map"
            prediction_map_path = input_dir + "prediction_map_" + str(image_number) + ".tif"
            
        
        
        # TODO: Read and append gt labels "gt" to "list_gt_labels" (flatten the array before appending)
        gt_path = 
        gt = 
    
    # TODO: Join all the predictions and ground truth labels using np.concatenate
    all_predictions = 
    all_gt_labels = 
    # TODO: Compute accuracy and confusion matrix
    accuracy = 
    conf_matrix = 
                     
    return accuracy, conf_matrix


def plot_confusion_matrix(conf_matrix):
    fig, ax = plt.subplots(figsize=(7.5, 7.5))
    ax.matshow(conf_matrix, cmap=plt.cm.Blues, alpha=0.5)
    for i in range(conf_matrix.shape[0]):
        for j in range(conf_matrix.shape[1]):
            ax.text(x=j, y=i,s=conf_matrix[i, j], va='center', ha='center', size='x-large')
    
    plt.xlabel('Predictions', fontsize=18)
    plt.ylabel('Ground Truth', fontsize=18)
    plt.title('Confusion Matrix', fontsize=18)
    plt.show()

## 7. Compute the accuracy, and confusion matrix of the images of the validation set

In [ ]:
# TODO: Compute and print the accuracy and confusion matrix of the images of the validation set 
#       (use the function predict_classification_maps_and_get_accuracy)


In [ ]:
# TODO: Visualize the confusion matrix using the function "plot_confusion_matrix", defined above


## 8. Search for good parameter values in the validation set

In [ ]:
# List of paramaters to evaluate in the validation set
n_estimators_values = [20, 50, 100, 200]
max_depth_values = [5, 10, 20, None]

##  9. Train classifier with best parameters found in the validation set, and classify the images of the test set

- Train the classifier with the parameters that obtain the best accuracy in the validation set
- Classify the images of the test set and save the prediction maps on disk. Use the function ***predict_classification_maps_and_get_accuracy*** with the parameter save_predictions=True

## 10. Visualize predictions

Visualize one of the classification predictions saved on disk

In [ ]:
import matplotlib.pyplot as plt

def display_label_image(label_map):
    colors = np.array([[255, 255, 255], # Impervious: white
                       [0, 0, 255],     # Building: Blue
                       [0, 255, 255],   # Low vegetation: cyan
                       [0, 255, 0]])    # Tree: green
    colors = colors.astype(np.uint8)
    color_map = np.zeros((label_map.shape[0], label_map.shape[1], 3)).astype(np.uint8)
    for label_id in range(colors.shape[0]):
        color_map[label_map == label_id] = colors[label_id, :]
    plt.figure(figsize = (11,11)) 
    plt.imshow(color_map)

In [ ]:
# TODO: display one of the prediction map images saved on disk


In [ ]:
# TODO: Display the ground truth corresponding to the image you visualized above


## 11. Answer the remaining questions of the PDF instructions file